In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

diabetes = pd.read_csv('diabetes.csv')

In [3]:
features = ['Pregnancies','PlasmaGlucose','DiastolicBloodPressure','TricepsThickness','SerumInsulin','BMI','DiabetesPedigree','Age']
target = 'Diabetic'
X, y = diabetes[features], diabetes[target]

In [4]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X[['Pregnancies', 'Age']], y, test_size=0.30, random_state=0, stratify=y)
print ('Treningowe obserwacje: %d\nTestowe obserwacje: %d' % (X_train.shape[0], X_test.shape[0]))

Treningowe obserwacje: 10500
Testowe obserwacje: 4500


In [5]:
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import StandardScaler

scaler_2var = StandardScaler()
X_train_standardized = scaler_2var.fit_transform(X_train)
X_test_standardized = scaler_2var.transform(X_test)

In [6]:
from sklearn.metrics import f1_score

### Zadanie: wizualizacja <br>

<font color = "green">

Poznaliśmy już pierwszy model dla regresji logistycznej, teraz sprawdź jak zachowuje się model dla różnych regularyzacji i ich stopnia. Zwizualizuj działanie modelu z wykorzystaniem funkcji plot_classification_surface oraz za każdym razem oblicz F1_score na zbiorze treningowym oraz testowym (zobaczysz czy model przypadkiem się nie przeucza).

Link do swoich wizualizacji prześlij Mentorowi.</font>

In [7]:
penalty = ['l1', 'l2', 'elasticnet', 'none']

C = [10**(-5), 10**(-4), 10**(-3), 0.01, 0.1, 1, 10, 100, 10**3, 10**4, 10**12]

In [8]:
models = []
scaler_2var = StandardScaler()
X_train_standardized = scaler_2var.fit_transform(X_train)
X_test_standardized = scaler_2var.transform(X_test)
models_param = []

for m in penalty:
    for n in C:
        if m == 'elasticnet':
            model_lr = LogisticRegression(penalty=m, C=n, solver="saga",l1_ratio=0)
            models_param.append((f'Penalty: {m}', f'C: {n}', f'l1_ratio: {0}'))
        elif m == 'none':
            model_lr = LogisticRegression(penalty=m, solver="saga")
            models_param.append((f'Penalty: {m}'))
        else:
            model_lr = LogisticRegression(penalty=m, C=n, solver="saga")
            models_param.append((f'Penalty: {m}', f'C: {n}'))
        models.append(model_lr.fit(X_train_standardized, y_train))
        

In [9]:
len(models)

44

In [10]:
models_predictions = []
for model in models:
    models_predictions.append(model.predict(X_test_standardized))

In [11]:
len(models_predictions)

44

In [12]:
from numpy import where
from numpy import meshgrid
from numpy import arange
from numpy import hstack

def plot_classification_surface(X_plot, y_plot, trained_model, m, n):
    
    # określenie granic zbioru
    min1, max1 = X_plot[:, 0].min()-1, X_plot[:, 0].max()+1
    min2, max2 = X_plot[:, 1].min()-1, X_plot[:, 1].max()+1

    # skalowanie dla obu osi
    x1grid = arange(min1, max1, 0.1)
    x2grid = arange(min2, max2, 0.1)

    # utworzenie siatki
    xx, yy = meshgrid(x1grid, x2grid)

    # przetworzenie siatki w wektor
    r1, r2 = xx.flatten(), yy.flatten()
    r1, r2 = r1.reshape((len(r1), 1)), r2.reshape((len(r2), 1))

    # stworzenie zmiennych objaśniających dla modelu
    grid = hstack((r1,r2))

    # predykcja modelu zbioru
    yhat = trained_model.predict(grid)

    # przetworzenie predykcji na decyzji dla konkretnego punktu wykresu
    zz = yhat.reshape(xx.shape)

    # wizualizacja siatki z przyporządkowaną klasą
    ax[m, n].contourf(xx, yy, zz, cmap='Paired')

    # tworzenie wykresu punktowego dla klas ze zbioru X
    for class_value in range(2):

        # przyporządkowanie klasy (y) do obsewacji (X)
        row_ix = where(y_plot == class_value)

        # stworzenie wykresu punktowego
        ax[m, n].scatter(X_plot[row_ix, 0], X_plot[row_ix, 1], cmap='Paired', alpha=0.3, label=class_value)


    # wizualizacja wykresu
    ax[m, n].legend(loc='upper right')

In [20]:
fig, ax = plt.subplots(int(len(models)/2 - 5), 2, figsize=(14, 82), dpi=300)
i = 0
none = False
c = int(len(models)/2 - 5)
print(c)
for a in range(0, c):
    for b in range(0, 2):
        m = a
        n = b
        if models_param[i] == "Penalty: none":
            if none == True:
                continue
            none = True
        plot_classification_surface(X_plot=X_train_standardized, y_plot=y_train, trained_model=models[i], m=m, n=n)
        ax[m, n].set_title(f'{models_param[i]} , F1_score: {np.round(f1_score(y_test, models_predictions[i]), 2)}', fontweight ="bold", fontsize=10)
        i += 1
    

17


Na podstawie wyników i wykresów uważam, że parametr C głównie odpowiada za zmianę w wynikach - F1_score. Dodatkowo rozumiem, że zmieniane parametry modelu mają wpływ jedynie na predykcję modelu (tło pomarańczowe / niebieskie). 

W żaden sposób nie zmienia się klasyfikacja względem obserwacji (kropki na wykresie) - co jest logiczne biorąc pod uwagę, że zmieniamy parametry modelu, a nie dane.

Rozumiem, że zmieniając parametr C staramy się zmienić "kształt" predykcji tak by rozdzielała poprawnie klasyfikacje względem obserwacji.

W głównej mierze w tym wypadku znaczenie ma jedynie parametr C. Dla skrajnych wartości C, model dla różnych "penalty" załamuje się i wartości oceny F1_score wynosi 0.

Ostatecznie jednak najlepszy wynik otrzymujemy dla wartości C = 0.01 lub braku parametru "penalty" - w tym wypadku parametr C nie występuje.